In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
#from mlxtend.plotting import plot_decision_regions

In [3]:
#!pip install xgboost catboost

In [4]:
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import confusion_matrix,classification_report,accuracy_score
from numpy import mean
from numpy import std
from sklearn.svm import SVC 
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score
from sklearn.tree import DecisionTreeClassifier
import xgboost as xgb
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from sklearn.ensemble import AdaBoostClassifier
from hyperopt import hp,fmin,tpe,STATUS_OK,Trials

In [5]:
from sklearn.model_selection import KFold, cross_val_score

In [6]:
path="./documents/DataSets/pd_speech_features.csv"
data = pd.read_csv(path)

In [7]:
data.shape

(757, 755)

In [8]:
data.head(5)

Unnamed: 0 Unnamed: 1 Baseline Features Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0         id     gender               PPE        DFA       RPDE  numPulses   
1          0          1           0.85247    0.71826    0.57227        240   
2          0          1           0.76686    0.69481    0.53966        234   
3          0          1           0.85083    0.67604    0.58982        232   
4          1          0           0.41121    0.79672    0.59257        178   

         Unnamed: 6        Unnamed: 7          Unnamed: 8    Unnamed: 9  ...  \
0  numPeriodsPulses  meanPeriodPulses  stdDevPeriodPulses  locPctJitter  ...   
1               239        0.00806353            8.68E-05       0.00218  ...   
2               233       0.008258256            7.31E-05       0.00195  ...   
3               231        0.00833959            6.04E-05       0.00176  ...   
4               177       0.010857733         0.000182739       0.00419  ...   

                Unnamed: 745               Unnamed: 746  \
0  tqwt_kurtosisValue_dec_28  tqwt_kurtosisValue_dec_29   
1                      1.562                     2.6445   
2                     1.5589                     3.6107   
3                     1.5643                     2.3308   
4                     3.7805                     3.5664   

                Unnamed: 747               Unnamed: 748  \
0  tqwt_kurtosisValue_dec_30  tqwt_kurtosisValue_dec_31   
1                     3.8686                     4.2105   
2                    23.5155                    14.1962   
3                     9.4959                    10.7458   
4                     5.2558                    14.0403   

                Unnamed: 749               Unnamed: 750  \
0  tqwt_kurtosisValue_dec_32  tqwt_kurtosisValue_dec_33   
1                     5.1221                     4.4625   
2                    11.0261                     9.5082   
3                    11.0177                     4.8066   
4                     4.2235                     4.6857   

                Unnamed: 751               Unnamed: 752  \
0  tqwt_kurtosisValue_dec_34  tqwt_kurtosisValue_dec_35   
1                     2.6202                     3.0004   
2                     6.5245                     6.3431   
3                     2.9199                     3.1495   
4                      4.846                      6.265   

                Unnamed: 753 Unnamed: 754  
0  tqwt_kurtosisValue_dec_36        class  
1                    18.9405            1  
2                     45.178            1  
3                     4.7666            1  
4                     4.0603            1  

[5 rows x 755 columns]

In [9]:
data.rename(columns=data.iloc[0], inplace = True)
data.drop([0], inplace = True)

In [10]:
#data.head(5)

In [11]:
data.reset_index(inplace = True, drop = True)

In [12]:
data.head(5)

id gender      PPE      DFA     RPDE numPulses numPeriodsPulses  \
0  0      1  0.85247  0.71826  0.57227       240              239   
1  0      1  0.76686  0.69481  0.53966       234              233   
2  0      1  0.85083  0.67604  0.58982       232              231   
3  1      0  0.41121  0.79672  0.59257       178              177   
4  1      0   0.3279  0.79782  0.53028       236              235   

  meanPeriodPulses stdDevPeriodPulses locPctJitter  ...  \
0       0.00806353           8.68E-05      0.00218  ...   
1      0.008258256           7.31E-05      0.00195  ...   
2       0.00833959           6.04E-05      0.00176  ...   
3      0.010857733        0.000182739      0.00419  ...   
4      0.008161574        0.002668863      0.00535  ...   

  tqwt_kurtosisValue_dec_28 tqwt_kurtosisValue_dec_29  \
0                     1.562                    2.6445   
1                    1.5589                    3.6107   
2                    1.5643                    2.3308   
3                    3.7805                    3.5664   
4                    6.1727                    5.8416   

  tqwt_kurtosisValue_dec_30 tqwt_kurtosisValue_dec_31  \
0                    3.8686                    4.2105   
1                   23.5155                   14.1962   
2                    9.4959                   10.7458   
3                    5.2558                   14.0403   
4                    6.0805                    5.7621   

  tqwt_kurtosisValue_dec_32 tqwt_kurtosisValue_dec_33  \
0                    5.1221                    4.4625   
1                   11.0261                    9.5082   
2                   11.0177                    4.8066   
3                    4.2235                    4.6857   
4                    7.7817                   11.6891   

  tqwt_kurtosisValue_dec_34 tqwt_kurtosisValue_dec_35  \
0                    2.6202                    3.0004   
1                    6.5245                    6.3431   
2                    2.9199                    3.1495   
3                     4.846                     6.265   
4                    8.2103                    5.0559   

  tqwt_kurtosisValue_dec_36 class  
0                   18.9405     1  
1                    45.178     1  
2                    4.7666     1  
3                    4.0603     1  
4                    6.1164     1  

[5 rows x 755 columns]

In [13]:
# check if any null value is present
data.isnull().values.any()

False

In [14]:
data_train = data.copy().drop(columns=["id"])
col_names = data_train.columns.tolist()
target_col = ["class"]
gender_col = ["gender"]
col_names.remove(target_col[0])
col_names.remove(gender_col[0])
data_train = data_train[col_names + target_col + gender_col]

In [15]:
#col_names

In [16]:
#data_train

In [17]:
len(data_train[col_names].columns)

752

In [18]:
from sklearn.preprocessing import StandardScaler
std = StandardScaler()

scaled = std.fit_transform(data_train[col_names])     # Standardize the columns to get them on the same scale
scaled = pd.DataFrame(scaled, columns=col_names)
#scaled
data_train = pd.concat([data_train[gender_col], scaled, data_train[target_col]], axis=1)

data_train.head(10)

gender       PPE       DFA      RPDE  numPulses  numPeriodsPulses  \
0      1  0.627644  0.256144  0.605835  -0.846892         -0.842373   
1      1  0.121620 -0.080433  0.368415  -0.907404         -0.902773   
2      1  0.617950 -0.349839  0.733609  -0.927575         -0.922907   
3      0 -1.980560  1.382279  0.753631  -1.472186         -1.466513   
4      0 -2.472989  1.398068  0.300123  -0.887233         -0.882640   
5      0 -1.409635  1.249084  1.204591  -0.988087         -1.023575   
6      1  0.086687 -1.133368  0.410424  -0.019891         -0.016898   
7      1  0.534490 -1.142841  0.165505  -0.060232         -0.057165   
8      1  0.366327 -1.187766  0.112211  -0.060232         -0.057165   
9      0  0.630895 -1.118728  0.433140   1.704710          1.704520   

   meanPeriodPulses  stdDevPeriodPulses  locPctJitter  locAbsJitter  ...  \
0          0.933328           -0.407251     -0.054993      0.037843  ...   
1          1.040014           -0.426092     -0.142570     -0.027698  ...   
2          1.084576           -0.443557     -0.214916     -0.088871  ...   
3          2.464215           -0.275316      0.710353      1.256919  ...   
4          0.987044            3.143597      1.152045      1.178269  ...   
5          0.696465            3.181440      2.096353      1.877380  ...   
6         -0.202175           -0.379107     -0.039762     -0.150043  ...   
7         -0.156774           -0.339951      0.188699      0.015996  ...   
8         -0.165906           -0.431317     -0.272032     -0.306032  ...   
9         -1.342185           -0.471748     -0.599493     -0.603155  ...   

   tqwt_kurtosisValue_dec_28  tqwt_kurtosisValue_dec_29  \
0                  -0.584822                  -0.619412   
1                  -0.584895                  -0.589778   
2                  -0.584767                  -0.629033   
3                  -0.532242                  -0.591137   
4                  -0.475545                  -0.521356   
5                  -0.508020                  -0.544917   
6                   2.157492                   1.609430   
7                  -0.530443                  -0.335822   
8                  -0.568184                  -0.504251   
9                  -0.582035                  -0.637725   

   tqwt_kurtosisValue_dec_30  tqwt_kurtosisValue_dec_31  \
0                  -0.576762                  -0.482286   
1                   0.193084                   0.016183   
2                  -0.356261                  -0.156055   
3                  -0.522406                   0.008400   
4                  -0.490090                  -0.404833   
5                  -0.453410                  -0.393127   
6                   0.527414                  -0.307797   
7                  -0.442733                  -0.474414   
8                  -0.555293                  -0.479505   
9                  -0.618175                  -0.517403   

   tqwt_kurtosisValue_dec_32  tqwt_kurtosisValue_dec_33  \
0                  -0.399331                  -0.484533   
1                  -0.067120                  -0.175566   
2                  -0.067593                  -0.463462   
3                  -0.449894                  -0.470865   
4                  -0.249678                  -0.042021   
5                  -0.394581                  -0.303152   
6                  -0.512774                  -0.474852   
7                  -0.482484                  -0.392774   
8                  -0.482968                  -0.529105   
9                  -0.503394                  -0.522559   

   tqwt_kurtosisValue_dec_34  tqwt_kurtosisValue_dec_35  \
0                  -0.775137                  -0.814727   
1                  -0.526647                  -0.582972   
2                  -0.756063                  -0.804390   
3                  -0.633475                  -0.588387   
4                  -0.419354                  -0.672216   
5                  -0.724533                  -0.779770   
6                  -

In [19]:
## Train Test Split
X = data_train[gender_col + col_names]      # Contains the independent columns 
y = data_train[target_col]     # Our target column

In [20]:
#print(X)

In [21]:
X.shape

(756, 753)

In [22]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=10)

In [23]:
y_train.value_counts()

class
1        395
0        134
dtype: int64

In [24]:
rf_classifier=RandomForestClassifier(random_state=10).fit(X_train,y_train)
prediction=rf_classifier.predict(X_test)

In [25]:
from sklearn.metrics import confusion_matrix,classification_report,accuracy_score
print(confusion_matrix(y_test,prediction))
print(accuracy_score(y_test,prediction))
print(classification_report(y_test,prediction))

[[ 39  19]
 [  3 166]]
0.9030837004405287
              precision    recall  f1-score   support

           0       0.93      0.67      0.78        58
           1       0.90      0.98      0.94       169

    accuracy                           0.90       227
   macro avg       0.91      0.83      0.86       227
weighted avg       0.91      0.90      0.90       227



**Randomized Search CV**

In [33]:
import numpy as np

# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt','log2']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 1000,10)]
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10,14]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4,6,8]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
              'criterion':['entropy','gini']}
print(random_grid)

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000], 'max_features': ['auto', 'sqrt', 'log2'], 'max_depth': [10, 120, 230, 340, 450, 560, 670, 780, 890, 1000], 'min_samples_split': [2, 5, 10, 14], 'min_samples_leaf': [1, 2, 4, 6, 8], 'criterion': ['entropy', 'gini']}


In [34]:
rf=RandomForestClassifier()
rf_randomcv=RandomizedSearchCV(estimator=rf,param_distributions=random_grid,n_iter=100,cv=3,verbose=2,
                               random_state=100,n_jobs=-1)
### fit the randomized model
rf_randomcv.fit(X_train,y_train)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:  1.1min
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:  4.8min
[Parallel(n_jobs=-1)]: Done 300 out of 300 | elapsed:  9.8min finished


RandomizedSearchCV(cv=3, estimator=RandomForestClassifier(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'criterion': ['entropy', 'gini'],
                                        'max_depth': [10, 120, 230, 340, 450,
                                                      560, 670, 780, 890,
                                                      1000],
                                        'max_features': ['auto', 'sqrt',
                                                         'log2'],
                                        'min_samples_leaf': [1, 2, 4, 6, 8],
                                        'min_samples_split': [2, 5, 10, 14],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=100, verbose=2)

In [35]:
rf_randomcv.best_params_

{'n_estimators': 1400,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 230,
 'criterion': 'gini'}

In [36]:
best_random_grid=rf_randomcv.best_estimator_

## Main Result

In [37]:
from sklearn.metrics import accuracy_score
y_pred=best_random_grid.predict(X_test)
print(confusion_matrix(y_test,y_pred))
print("Accuracy Score {}".format(accuracy_score(y_test,y_pred)))
print("Classification report: {}".format(classification_report(y_test,y_pred)))

[[ 40  18]
 [  3 166]]
Accuracy Score 0.9074889867841409
Classification report:               precision    recall  f1-score   support

           0       0.93      0.69      0.79        58
           1       0.90      0.98      0.94       169

    accuracy                           0.91       227
   macro avg       0.92      0.84      0.87       227
weighted avg       0.91      0.91      0.90       227



In [41]:
from sklearn.metrics import f1_score
print(f1_score(y_test, y_pred, average="micro"))

0.9074889867841409


**Grid Search CV**

In [38]:
rf_randomcv.best_params_

{'n_estimators': 1400,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 230,
 'criterion': 'gini'}

In [39]:
from sklearn.model_selection import GridSearchCV

param_grid = {
    'criterion': [rf_randomcv.best_params_['criterion']],
    'max_depth': [rf_randomcv.best_params_['max_depth']],
    'max_features': [rf_randomcv.best_params_['max_features']],
    'min_samples_leaf': [rf_randomcv.best_params_['min_samples_leaf'], 
                         rf_randomcv.best_params_['min_samples_leaf']+2, 
                         rf_randomcv.best_params_['min_samples_leaf'] + 4],
    'min_samples_split': [rf_randomcv.best_params_['min_samples_split'] - 2,
                          rf_randomcv.best_params_['min_samples_split'] - 1,
                          rf_randomcv.best_params_['min_samples_split'], 
                          rf_randomcv.best_params_['min_samples_split'] +1,
                          rf_randomcv.best_params_['min_samples_split'] + 2],
    'n_estimators': [rf_randomcv.best_params_['n_estimators'] - 200, rf_randomcv.best_params_['n_estimators'] - 100, 
                     rf_randomcv.best_params_['n_estimators'], 
                     rf_randomcv.best_params_['n_estimators'] + 100, rf_randomcv.best_params_['n_estimators'] + 200]
}

print(param_grid)

{'criterion': ['gini'], 'max_depth': [230], 'max_features': ['sqrt'], 'min_samples_leaf': [1, 3, 5], 'min_samples_split': [0, 1, 2, 3, 4], 'n_estimators': [1200, 1300, 1400, 1500, 1600]}


In [40]:
#### Fit the grid_search to the data
rf=RandomForestClassifier()
grid_search=GridSearchCV(estimator=rf,param_grid=param_grid,cv=10,n_jobs=-1,verbose=2)
grid_search.fit(X_train,y_train)

Fitting 10 folds for each of 75 candidates, totalling 750 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:    9.0s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:  3.6min
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed: 10.5min
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed: 19.7min
[Parallel(n_jobs=-1)]: Done 750 out of 750 | elapsed: 24.6min finished


GridSearchCV(cv=10, estimator=RandomForestClassifier(), n_jobs=-1,
             param_grid={'criterion': ['gini'], 'max_depth': [230],
                         'max_features': ['sqrt'],
                         'min_samples_leaf': [1, 3, 5],
                         'min_samples_split': [0, 1, 2, 3, 4],
                         'n_estimators': [1200, 1300, 1400, 1500, 1600]},
             verbose=2)

In [57]:
grid_search.best_params_

{'criterion': 'gini',
 'max_depth': 230,
 'max_features': 'sqrt',
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 1200}

In [42]:
grid_search.best_estimator_

RandomForestClassifier(max_depth=230, max_features='sqrt', n_estimators=1200)

In [43]:
best_grid=grid_search.best_estimator_

In [44]:
best_grid #(max_depth=670, min_samples_split=3, n_estimators=2200)

RandomForestClassifier(max_depth=230, max_features='sqrt', n_estimators=1200)

In [45]:
y_pred1=best_grid.predict(X_test)
print(confusion_matrix(y_test,y_pred1))
print("Accuracy Score {}".format(accuracy_score(y_test,y_pred1)))
print("Classification report: {}".format(classification_report(y_test,y_pred1)))

[[ 39  19]
 [  3 166]]
Accuracy Score 0.9030837004405287
Classification report:               precision    recall  f1-score   support

           0       0.93      0.67      0.78        58
           1       0.90      0.98      0.94       169

    accuracy                           0.90       227
   macro avg       0.91      0.83      0.86       227
weighted avg       0.91      0.90      0.90       227



In [46]:
from sklearn.metrics import f1_score
print(f1_score(y_test, y_pred1, average="micro"))

0.9030837004405287


# K-Nearest Neighbour

In [26]:
X_traine, X_teste, y_traine, y_teste = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=12)

In [27]:
knn = KNeighborsClassifier()

In [28]:
knn.fit(X_traine,y_traine)

KNeighborsClassifier()

In [29]:
pred1 = knn.predict(X_teste)
print(confusion_matrix(y_teste,pred1))
print("Accuracy Score {}".format(accuracy_score(y_teste,pred1)))
print("Classification report: {}".format(classification_report(y_teste,pred1)))

[[ 25  33]
 [ 11 158]]
Accuracy Score 0.8061674008810573
Classification report:               precision    recall  f1-score   support

           0       0.69      0.43      0.53        58
           1       0.83      0.93      0.88       169

    accuracy                           0.81       227
   macro avg       0.76      0.68      0.70       227
weighted avg       0.79      0.81      0.79       227



In [30]:
from sklearn.metrics import f1_score
print(f1_score(y_teste, pred1, average="micro"))

0.8061674008810573


In [31]:
k_range = list(range(1,40))
weight_options = ["uniform", "distance"]
metric=["euclidean", "manhattan"]
param_grid = dict(n_neighbors = k_range, weights = weight_options, metric= metric)
grid = GridSearchCV(estimator=knn, param_grid=param_grid, cv = 10, scoring = 'accuracy', n_jobs=-1, verbose=2 )
grid.fit(X_traine,y_traine)

Fitting 10 folds for each of 156 candidates, totalling 1560 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:    6.1s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:   11.2s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:   20.8s
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:   34.1s
[Parallel(n_jobs=-1)]: Done 997 tasks      | elapsed:   52.3s
[Parallel(n_jobs=-1)]: Done 1442 tasks      | elapsed:  1.2min
[Parallel(n_jobs=-1)]: Done 1560 out of 1560 | elapsed:  1.3min finished


GridSearchCV(cv=10, estimator=KNeighborsClassifier(), n_jobs=-1,
             param_grid={'metric': ['euclidean', 'manhattan'],
                         'n_neighbors': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12,
                                         13, 14, 15, 16, 17, 18, 19, 20, 21, 22,
                                         23, 24, 25, 26, 27, 28, 29, 30, ...],
                         'weights': ['uniform', 'distance']},
             scoring='accuracy', verbose=2)

In [32]:
grid.best_estimator_

KNeighborsClassifier(metric='manhattan', n_neighbors=1)

In [33]:
knngrid=grid.best_estimator_

In [34]:
pred = knngrid.predict(X_teste)
print(confusion_matrix(y_teste,pred))
print("Accuracy Score {}".format(accuracy_score(y_teste,pred)))
print("Classification report: {}".format(classification_report(y_teste,pred)))

[[ 54   4]
 [ 10 159]]
Accuracy Score 0.9383259911894273
Classification report:               precision    recall  f1-score   support

           0       0.84      0.93      0.89        58
           1       0.98      0.94      0.96       169

    accuracy                           0.94       227
   macro avg       0.91      0.94      0.92       227
weighted avg       0.94      0.94      0.94       227



In [35]:
from sklearn.metrics import f1_score
print(f1_score(y_teste, pred, average="micro"))

0.9383259911894273


# Support Vector Machine

In [83]:
X_train1, X_test1, y_train1, y_test1 = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=14)

### No hyperparameter tuning

In [84]:
svm1= SVC()
svm1.fit(X_train1, y_train1)

SVC()

In [85]:
preda = svm1.predict(X_test1)
print(confusion_matrix(y_test1,preda))
print("Accuracy Score {}".format(accuracy_score(y_test1,preda)))
print("Classification report: {}".format(classification_report(y_test1,preda)))

[[ 28  30]
 [  5 164]]
Accuracy Score 0.8458149779735683
Classification report:               precision    recall  f1-score   support

           0       0.85      0.48      0.62        58
           1       0.85      0.97      0.90       169

    accuracy                           0.85       227
   macro avg       0.85      0.73      0.76       227
weighted avg       0.85      0.85      0.83       227



In [86]:
from sklearn.metrics import f1_score
print(f1_score(y_test1, preda, average="micro"))

0.8458149779735682


### Trying hyperparameter tuning

In [87]:
svm = SVC(C=100, gamma= 0.001)
svm.fit(X_train1, y_train1)

SVC(C=100, gamma=0.001)

In [88]:
predact = svm.predict(X_test1)
print(confusion_matrix(y_test1,predact))
print("Accuracy Score {}".format(accuracy_score(y_test1,predact)))
print("Classification report: {}".format(classification_report(y_test1,predact)))

[[ 39  19]
 [  7 162]]
Accuracy Score 0.8854625550660793
Classification report:               precision    recall  f1-score   support

           0       0.85      0.67      0.75        58
           1       0.90      0.96      0.93       169

    accuracy                           0.89       227
   macro avg       0.87      0.82      0.84       227
weighted avg       0.88      0.89      0.88       227



In [89]:
from sklearn.metrics import f1_score
print(f1_score(y_test1, predact, average="micro"))

0.8854625550660793


### after 7 fold cv(calculated using the below code)

In [237]:
#cv = KFold(n_splits=7, random_state=1, shuffle=True)

In [238]:
#scores = cross_val_score(svm, X_train1, y_train1, scoring='accuracy', cv=cv, n_jobs=-1)

In [239]:
#print('Accuracy: %.3f (%.3f)' % (mean(scores), std(scores)))

Accuracy: 0.873 (0.033)


## Code to check best kfold accuracies

In [41]:
# sensitivity analysis of k in k-fold cross-validation
from sklearn.model_selection import LeaveOneOut

# evaluate the model using a given test condition
def evaluate_model(cv):
    # get the model
    model = svm
    # evaluate the model
    scores = cross_val_score(model, X_train1, y_train1, scoring='accuracy', cv=cv, n_jobs=-1)
    # return scores
    return mean(scores), scores.min(), scores.max()

### calculate the ideal test condition
ideal, _, _ = evaluate_model(LeaveOneOut())
print('Ideal: %.3f' % ideal)
### define folds to test
folds = range(2,31)
### record mean and min/max of each set of results
means, mins, maxs = list(),list(),list()
### evaluate each k value
for k in folds:
    # define the test condition
    cv = KFold(n_splits=k, shuffle=True, random_state=1)
    # evaluate k value
    k_mean, k_min, k_max = evaluate_model(cv)
    # report performance
    print('> folds=%d, accuracy=%.3f (%.3f,%.3f)' % (k, k_mean, k_min, k_max))
    # store mean accuracy
    means.append(k_mean)
    # store min and max relative to the mean
    mins.append(k_mean - k_min)
    maxs.append(k_max - k_mean)


Ideal: 0.883
> folds=2, accuracy=0.860 (0.845,0.875)
> folds=3, accuracy=0.860 (0.841,0.876)
> folds=4, accuracy=0.871 (0.848,0.910)
> folds=5, accuracy=0.855 (0.792,0.915)
> folds=6, accuracy=0.860 (0.830,0.910)
> folds=7, accuracy=0.851 (0.789,0.895)
> folds=8, accuracy=0.854 (0.818,0.881)
> folds=9, accuracy=0.862 (0.780,0.931)
> folds=10, accuracy=0.860 (0.811,0.925)
> folds=11, accuracy=0.875 (0.792,0.918)
> folds=12, accuracy=0.866 (0.795,0.933)
> folds=13, accuracy=0.858 (0.750,0.950)
> folds=14, accuracy=0.868 (0.789,0.921)
> folds=15, accuracy=0.869 (0.800,0.917)
> folds=16, accuracy=0.873 (0.727,0.939)
> folds=17, accuracy=0.877 (0.710,0.968)
> folds=18, accuracy=0.871 (0.767,0.933)
> folds=19, accuracy=0.870 (0.786,0.964)
> folds=20, accuracy=0.866 (0.731,0.963)
> folds=21, accuracy=0.867 (0.680,0.962)
> folds=22, accuracy=0.875 (0.708,1.000)
> folds=23, accuracy=0.875 (0.696,1.000)
> folds=24, accuracy=0.869 (0.773,1.000)
> folds=25, accuracy=0.879 (0.714,1.000)
> folds=26,

## Naive Bayes

In [22]:
X_train2, X_test2, y_train2, y_test2 = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=16)

In [23]:
NB= GaussianNB(var_smoothing=1).fit(X_train2, y_train2)
predb = NB.predict(X_test2)
print(confusion_matrix(y_test2,predb))
print("Accuracy Score {}".format(accuracy_score(y_test2,predb)))
print("Classification report: {}".format(classification_report(y_test2,predb)))

[[ 40  18]
 [ 18 151]]
Accuracy Score 0.8414096916299559
Classification report:               precision    recall  f1-score   support

           0       0.69      0.69      0.69        58
           1       0.89      0.89      0.89       169

    accuracy                           0.84       227
   macro avg       0.79      0.79      0.79       227
weighted avg       0.84      0.84      0.84       227



In [24]:
from sklearn.metrics import f1_score
print(f1_score(y_test2, predb, average="micro"))

0.8414096916299559


In [32]:
c=AdaBoostClassifier(NB,learning_rate=0.0000001).fit(X_train2,y_train2)
c.score(X_test2, y_test2)

0.8414096916299559

## Logistic Reression

In [103]:
X_train3, X_test3, y_train3, y_test3 = train_test_split(X, y, stratify=y,  test_size = 0.30, random_state=18)

In [106]:
y_train3.value_counts()

class
1        395
0        134
dtype: int64

In [107]:
lr = LogisticRegression().fit(X_train3, y_train3)

In [108]:
predlr = lr.predict(X_test3)
print(confusion_matrix(y_test3,predlr))
print("Accuracy Score {}".format(accuracy_score(y_test3,predlr)))
print("Classification report: {}".format(classification_report(y_test3,predlr)))
print(f1_score(y_test3, predlr, average="micro"))

[[ 35  23]
 [ 13 156]]
Accuracy Score 0.8414096916299559
Classification report:               precision    recall  f1-score   support

           0       0.73      0.60      0.66        58
           1       0.87      0.92      0.90       169

    accuracy                           0.84       227
   macro avg       0.80      0.76      0.78       227
weighted avg       0.84      0.84      0.84       227

0.8414096916299559


In [109]:
iterations = [100,70,200,250]
#param_grid = dict(max_iter=iterations)
c_space = np.logspace(-5, 8, 15)
param_gridlr = {'C': c_space, 'max_iter':iterations}

In [110]:
gridlr = GridSearchCV(lr , param_gridlr, n_jobs=-1,verbose=5, cv=10)
gridlr.fit(X_train3, y_train3)

Fitting 10 folds for each of 60 candidates, totalling 600 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 tasks      | elapsed:    2.7s
[Parallel(n_jobs=-1)]: Done  56 tasks      | elapsed:    3.6s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:    5.1s
[Parallel(n_jobs=-1)]: Done 272 tasks      | elapsed:    9.2s
[Parallel(n_jobs=-1)]: Done 434 tasks      | elapsed:   16.1s
[Parallel(n_jobs=-1)]: Done 600 out of 600 | elapsed:   19.9s finished


GridSearchCV(cv=10, estimator=LogisticRegression(), n_jobs=-1,
             param_grid={'C': array([1.00000000e-05, 8.48342898e-05, 7.19685673e-04, 6.10540230e-03,
       5.17947468e-02, 4.39397056e-01, 3.72759372e+00, 3.16227766e+01,
       2.68269580e+02, 2.27584593e+03, 1.93069773e+04, 1.63789371e+05,
       1.38949549e+06, 1.17876863e+07, 1.00000000e+08]),
                         'max_iter': [100, 70, 200, 250]},
             verbose=5)

In [111]:
loki=gridlr.best_estimator_

In [112]:
loki

LogisticRegression(C=0.006105402296585327)

In [113]:
predlr1 = loki.predict(X_test3)
print(confusion_matrix(y_test3,predlr1))
print("Accuracy Score {}".format(accuracy_score(y_test3,predlr1)))
print("Classification report: {}".format(classification_report(y_test3,predlr1)))
print(f1_score(y_test3, predlr1, average="micro"))

[[ 36  22]
 [  4 165]]
Accuracy Score 0.8854625550660793
Classification report:               precision    recall  f1-score   support

           0       0.90      0.62      0.73        58
           1       0.88      0.98      0.93       169

    accuracy                           0.89       227
   macro avg       0.89      0.80      0.83       227
weighted avg       0.89      0.89      0.88       227

0.8854625550660793


## Decision Tree

In [33]:
X_train4, X_test4, y_train4, y_test4 = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=20)

In [34]:
dtree=DecisionTreeClassifier(random_state=10).fit(X_train4, y_train4)

In [35]:
preddt = dtree.predict(X_test4)
print(confusion_matrix(y_test4,preddt))
print("Accuracy Score {}".format(accuracy_score(y_test4,preddt)))
print("Classification report: {}".format(classification_report(y_test4,preddt)))
print(f1_score(y_test4, preddt, average="micro"))

[[ 33  25]
 [ 40 129]]
Accuracy Score 0.7136563876651982
Classification report:               precision    recall  f1-score   support

           0       0.45      0.57      0.50        58
           1       0.84      0.76      0.80       169

    accuracy                           0.71       227
   macro avg       0.64      0.67      0.65       227
weighted avg       0.74      0.71      0.72       227

0.7136563876651982


### Grid search cv

In [36]:
# Number of features to consider at every split
max_features = ['auto', 'sqrt','log2']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 1000,10)]
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 14]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4,6,8]
# Create the random grid
random_grid1 = {
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
              'criterion':['entropy','gini']}
print(random_grid1)

{'max_features': ['auto', 'sqrt', 'log2'], 'max_depth': [10, 120, 230, 340, 450, 560, 670, 780, 890, 1000], 'min_samples_split': [2, 5, 10, 14], 'min_samples_leaf': [1, 2, 4, 6, 8], 'criterion': ['entropy', 'gini']}


In [37]:
dtree_randomcv=GridSearchCV(estimator=dtree,param_grid=random_grid1,cv=10,verbose=2,n_jobs=-1)
### fit the randomized model
dtree_randomcv.fit(X_train4,y_train4)

Fitting 10 folds for each of 1200 candidates, totalling 12000 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  25 tasks      | elapsed:    6.0s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:    8.4s
[Parallel(n_jobs=-1)]: Done 349 tasks      | elapsed:   13.3s
[Parallel(n_jobs=-1)]: Done 632 tasks      | elapsed:   20.1s
[Parallel(n_jobs=-1)]: Done 997 tasks      | elapsed:   28.8s
[Parallel(n_jobs=-1)]: Done 1442 tasks      | elapsed:   38.8s
[Parallel(n_jobs=-1)]: Done 1969 tasks      | elapsed:   50.8s
[Parallel(n_jobs=-1)]: Done 2576 tasks      | elapsed:  1.1min
[Parallel(n_jobs=-1)]: Done 3265 tasks      | elapsed:  1.4min
[Parallel(n_jobs=-1)]: Done 4034 tasks      | elapsed:  1.6min
[Parallel(n_jobs=-1)]: Done 4885 tasks      | elapsed:  2.0min
[Parallel(n_jobs=-1)]: Done 5816 tasks      | elapsed:  2.3min
[Parallel(n_jobs=-1)]: Done 6829 tasks      | elapsed:  2.7min
[Parallel(n_jobs=-1)]: Done 7922 tasks      | elapsed:  3.1min
[Parallel(n_jobs=-1)]: Done 9097 tasks      | e

GridSearchCV(cv=10, estimator=DecisionTreeClassifier(random_state=10),
             n_jobs=-1,
             param_grid={'criterion': ['entropy', 'gini'],
                         'max_depth': [10, 120, 230, 340, 450, 560, 670, 780,
                                       890, 1000],
                         'max_features': ['auto', 'sqrt', 'log2'],
                         'min_samples_leaf': [1, 2, 4, 6, 8],
                         'min_samples_split': [2, 5, 10, 14]},
             verbose=2)

In [38]:
dtree_randomcv.best_params_

{'criterion': 'entropy',
 'max_depth': 120,
 'max_features': 'auto',
 'min_samples_leaf': 6,
 'min_samples_split': 2}

In [39]:
preddt2 = dtree_randomcv.best_estimator_.predict(X_test4)
print(confusion_matrix(y_test4,preddt2))
print("Accuracy Score {}".format(accuracy_score(y_test4,preddt2)))
print("Classification report: {}".format(classification_report(y_test4,preddt2)))
print(f1_score(y_test4, preddt2, average="micro"))

[[ 32  26]
 [ 19 150]]
Accuracy Score 0.801762114537445
Classification report:               precision    recall  f1-score   support

           0       0.63      0.55      0.59        58
           1       0.85      0.89      0.87       169

    accuracy                           0.80       227
   macro avg       0.74      0.72      0.73       227
weighted avg       0.79      0.80      0.80       227

0.801762114537445


In [82]:
d=AdaBoostClassifier(dtree_randomcv.best_estimator_,learning_rate=0.01, n_estimators=40,random_state=1).fit(X_train4,y_train4)
preddt3 = d.predict(X_test4)
print(confusion_matrix(y_test4,preddt3))
print("Accuracy Score {}".format(accuracy_score(y_test4,preddt3)))
print("Classification report: {}".format(classification_report(y_test4,preddt3)))
print(f1_score(y_test4, preddt3, average="micro"))

[[ 34  24]
 [  5 164]]
Accuracy Score 0.8722466960352423
Classification report:               precision    recall  f1-score   support

           0       0.87      0.59      0.70        58
           1       0.87      0.97      0.92       169

    accuracy                           0.87       227
   macro avg       0.87      0.78      0.81       227
weighted avg       0.87      0.87      0.86       227

0.8722466960352423


## XGBoost

In [36]:
X_encoded=pd.get_dummies(X, columns= ['gender'])

In [37]:
X_train5, X_test5, y_train5, y_test5 = train_test_split(X_encoded, y, stratify=y, test_size = 0.30, random_state=22)

In [38]:
classifier1=xgb.XGBClassifier(random_state=22)

In [39]:
classifier1.fit(X_train5, y_train5)

[19:01:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=1, gamma=0, gpu_id=-1,
              importance_type='gain', interaction_constraints='',
              learning_rate=0.300000012, max_delta_step=0, max_depth=6,
              min_child_weight=1, missing=nan, monotone_constraints='()',
              n_estimators=100, n_jobs=8, num_parallel_tree=1, random_state=22,
              reg_alpha=0, reg_lambda=1, scale_pos_weight=1, subsample=1,
              tree_method='exact', validate_parameters=1, verbosity=None)

In [40]:
predxg = classifier1.predict(X_test5)
print(confusion_matrix(y_test5,predxg))
print("Accuracy Score {}".format(accuracy_score(y_test5,predxg)))
print("Classification report: {}".format(classification_report(y_test5,predxg)))
print(f1_score(y_test5, predxg, average="micro"))

[[ 37  21]
 [  5 164]]
Accuracy Score 0.8854625550660793
Classification report:               precision    recall  f1-score   support

           0       0.88      0.64      0.74        58
           1       0.89      0.97      0.93       169

    accuracy                           0.89       227
   macro avg       0.88      0.80      0.83       227
weighted avg       0.89      0.89      0.88       227

0.8854625550660793


### Hyperopt

In [137]:
def objective(space):

    warnings.filterwarnings(action='ignore')
    classifier2 = xgb.XGBClassifier(n_estimators = space['n_estimators'],
                            max_depth = int(space['max_depth']),
                            learning_rate = space['learning_rate'],
                            gamma = space['gamma'],
                            min_child_weight = space['min_child_weight'],
                            subsample = space['subsample'],
                            colsample_bytree = space['colsample_bytree']
                            )
    
    classifier2.fit(X_train5, y_train5)

    # Applying k-Fold Cross Validation
    from sklearn.model_selection import cross_val_score
    accuracies = cross_val_score(estimator = classifier2, X = X_train5, y = y_train5, cv = 10)
   # accuracy = cross_val_score(classifier2, X_train5, y_train5, cv = 5).mean()
    CrossValMean = accuracies.mean()
    print("CrossValMean:", CrossValMean)
        # We aim to maximize accuracy, therefore we return it as a negative value
   # return {'loss': -accuracy, 'status': STATUS_OK }
    return{'loss':1-CrossValMean, 'status': STATUS_OK }

space = {
    'max_depth' : hp.choice('max_depth', range(5, 30, 1)),
    'learning_rate' : hp.quniform('learning_rate', 0.01, 0.5, 0.01),
    'n_estimators' : hp.choice('n_estimators', range(20, 205, 5)),
    'gamma' : hp.quniform('gamma', 0, 0.50, 0.01),
    'min_child_weight' : hp.quniform('min_child_weight', 1, 10, 1),
    'subsample' : hp.quniform('subsample', 0.1, 1, 0.01),
    'colsample_bytree' : hp.quniform('colsample_bytree', 0.1, 1.0, 0.01)}

trials = Trials()
best = fmin(fn=objective,
            space=space,
            algo=tpe.suggest,
            max_evals=80,
            trials=trials)

print("Best: ", best)



[21:57:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:57:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:57:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:58:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[21:58:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:58:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:58:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:58:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[21:59:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:59:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[21:59:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:00:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[22:00:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:00:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CrossValMean:                                                                                                          
0.8108853410740202                                                                                                     
[22:00:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default

[22:01:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:01:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:01:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:01:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[22:21:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:21:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:21:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:21:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[22:21:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:21:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CrossValMean:                                                                                                          
0.856422351233672                                                                                                      
[22:21:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default

[22:23:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:23:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:23:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:23:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[22:24:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:24:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:24:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:24:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[22:24:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[22:24:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CrossValMean:                                                                                                          
0.8808780841799709                                                                                                     
[22:25:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default

In [138]:
# Fitting XGBoost to the Training set
from xgboost import XGBClassifier
classifier4 = XGBClassifier(n_estimators = best['n_estimators'],
                            max_depth = best['max_depth'],
                            learning_rate = best['learning_rate'],
                            gamma = best['gamma'],
                            min_child_weight = best['min_child_weight'],
                            subsample = best['subsample'],
                            colsample_bytree = best['colsample_bytree']
                            )

classifier4.fit(X_train5, y_train5)

[22:27:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=0.21,
              gamma=0.35000000000000003, gpu_id=-1, importance_type='gain',
              interaction_constraints='', learning_rate=0.06, max_delta_step=0,
              max_depth=4, min_child_weight=5.0, missing=nan,
              monotone_constraints='()', n_estimators=25, n_jobs=8,
              num_parallel_tree=1, random_state=0, reg_alpha=0, reg_lambda=1,
              scale_pos_weight=1, subsample=0.98, tree_method='exact',
              validate_parameters=1, verbosity=None)

In [139]:
predxg111 = classifier4.predict(X_test5)
print(confusion_matrix(y_test5,predxg111))
print("Accuracy Score {}".format(accuracy_score(y_test5,predxg111)))
print("Classification report: {}".format(classification_report(y_test5,predxg111)))
print(f1_score(y_test5, predxg111, average="micro"))

[[ 34  24]
 [  2 167]]
Accuracy Score 0.8854625550660793
Classification report:               precision    recall  f1-score   support

           0       0.94      0.59      0.72        58
           1       0.87      0.99      0.93       169

    accuracy                           0.89       227
   macro avg       0.91      0.79      0.83       227
weighted avg       0.89      0.89      0.88       227

0.8854625550660793


## CatBoost

In [24]:
X_train6, X_test6, y_train6, y_test6 = train_test_split(X, y, stratify=y, test_size = 0.30, random_state=30)

0.8458149779735683 without hyperparameter tuning

### after optuna

In [25]:
categorical_features_indices = np.where(X.dtypes != np.float)[0]

In [196]:
ca1=CatBoostClassifier(l2_leaf_reg = 3,
    iterations = 1000,
    fold_len_multiplier = 1.05,
    learning_rate = 0.05,
    custom_loss = ['Accuracy'],
    random_seed = 100,
    depth=8,                 
    loss_function = 'Logloss',
    early_stopping_rounds=100,
    eval_metric='AUC'
                      )

In [197]:
ca1.fit(
    X_train6, y_train6,
    cat_features = categorical_features_indices,
    eval_set=(X_test6, y_test6),  # you can uncomment this for text output
    plot = True
)


MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	test: 0.7591308	best: 0.7591308 (0)	total: 269ms	remaining: 4m 28s
1:	test: 0.8367170	best: 0.8367170 (1)	total: 542ms	remaining: 4m 30s
2:	test: 0.8489594	best: 0.8489594 (2)	total: 806ms	remaining: 4m 27s
3:	test: 0.8503367	best: 0.8503367 (3)	total: 1.05s	remaining: 4m 22s
4:	test: 0.8530912	best: 0.8530912 (4)	total: 1.34s	remaining: 4m 26s
5:	test: 0.8776780	best: 0.8776780 (5)	total: 1.6s	remaining: 4m 25s
6:	test: 0.8753316	best: 0.8776780 (5)	total: 1.85s	remaining: 4m 23s
7:	test: 0.8794124	best: 0.8794124 (7)	total: 2.1s	remaining: 4m 20s
8:	test: 0.8763518	best: 0.8794124 (7)	total: 2.34s	remaining: 4m 17s
9:	test: 0.8694144	best: 0.8794124 (7)	total: 2.59s	remaining: 4m 16s
10:	test: 0.8766578	best: 0.8794124 (7)	total: 2.83s	remaining: 4m 14s
11:	test: 0.8854315	best: 0.8854315 (11)	total: 3.07s	remaining: 4m 12s
12:	test: 0.8918588	best: 0.8918588 (12)	total: 3.31s	remaining: 4m 11s
13:	test: 0.8994083	best: 0.8994083 (13)	total: 3.56s	remaining: 4m 10s
14:	test: 0.903

115:	test: 0.9389920	best: 0.9406244 (108)	total: 33s	remaining: 4m 11s
116:	test: 0.9391961	best: 0.9406244 (108)	total: 33.3s	remaining: 4m 11s
117:	test: 0.9387880	best: 0.9406244 (108)	total: 33.6s	remaining: 4m 11s
118:	test: 0.9394001	best: 0.9406244 (108)	total: 33.9s	remaining: 4m 11s
119:	test: 0.9388900	best: 0.9406244 (108)	total: 34.3s	remaining: 4m 11s
120:	test: 0.9394001	best: 0.9406244 (108)	total: 34.6s	remaining: 4m 11s
121:	test: 0.9395021	best: 0.9406244 (108)	total: 34.9s	remaining: 4m 11s
122:	test: 0.9398082	best: 0.9406244 (108)	total: 35.2s	remaining: 4m 11s
123:	test: 0.9399102	best: 0.9406244 (108)	total: 35.6s	remaining: 4m 11s
124:	test: 0.9399102	best: 0.9406244 (108)	total: 35.9s	remaining: 4m 11s
125:	test: 0.9405223	best: 0.9406244 (108)	total: 36.2s	remaining: 4m 11s
126:	test: 0.9399102	best: 0.9406244 (108)	total: 36.5s	remaining: 4m 10s
127:	test: 0.9397062	best: 0.9406244 (108)	total: 36.9s	remaining: 4m 11s
128:	test: 0.9405223	best: 0.9406244 (10

228:	test: 0.9500102	best: 0.9500102 (228)	total: 1m 9s	remaining: 3m 53s
229:	test: 0.9500102	best: 0.9500102 (228)	total: 1m 9s	remaining: 3m 53s
230:	test: 0.9499082	best: 0.9500102 (228)	total: 1m 10s	remaining: 3m 53s
231:	test: 0.9499082	best: 0.9500102 (228)	total: 1m 10s	remaining: 3m 53s
232:	test: 0.9503163	best: 0.9503163 (232)	total: 1m 10s	remaining: 3m 52s
233:	test: 0.9500102	best: 0.9503163 (232)	total: 1m 11s	remaining: 3m 52s
234:	test: 0.9499082	best: 0.9503163 (232)	total: 1m 11s	remaining: 3m 52s
235:	test: 0.9498062	best: 0.9503163 (232)	total: 1m 11s	remaining: 3m 52s
236:	test: 0.9498062	best: 0.9503163 (232)	total: 1m 12s	remaining: 3m 51s
237:	test: 0.9502142	best: 0.9503163 (232)	total: 1m 12s	remaining: 3m 51s
238:	test: 0.9501122	best: 0.9503163 (232)	total: 1m 12s	remaining: 3m 51s
239:	test: 0.9506223	best: 0.9506223 (239)	total: 1m 12s	remaining: 3m 50s
240:	test: 0.9503163	best: 0.9506223 (239)	total: 1m 13s	remaining: 3m 50s
241:	test: 0.9502142	best: 

338:	test: 0.9549072	best: 0.9551112 (337)	total: 1m 45s	remaining: 3m 26s
339:	test: 0.9552132	best: 0.9552132 (339)	total: 1m 46s	remaining: 3m 25s
340:	test: 0.9551112	best: 0.9552132 (339)	total: 1m 46s	remaining: 3m 25s
341:	test: 0.9551112	best: 0.9552132 (339)	total: 1m 46s	remaining: 3m 25s
342:	test: 0.9549072	best: 0.9552132 (339)	total: 1m 47s	remaining: 3m 25s
343:	test: 0.9547031	best: 0.9552132 (339)	total: 1m 47s	remaining: 3m 25s
344:	test: 0.9547031	best: 0.9552132 (339)	total: 1m 47s	remaining: 3m 24s
345:	test: 0.9548051	best: 0.9552132 (339)	total: 1m 48s	remaining: 3m 24s
346:	test: 0.9548051	best: 0.9552132 (339)	total: 1m 48s	remaining: 3m 24s
347:	test: 0.9548051	best: 0.9552132 (339)	total: 1m 48s	remaining: 3m 23s
348:	test: 0.9549072	best: 0.9552132 (339)	total: 1m 49s	remaining: 3m 23s
349:	test: 0.9550092	best: 0.9552132 (339)	total: 1m 49s	remaining: 3m 23s
350:	test: 0.9554173	best: 0.9554173 (350)	total: 1m 49s	remaining: 3m 23s
351:	test: 0.9553152	best

449:	test: 0.9566415	best: 0.9568455 (407)	total: 2m 21s	remaining: 2m 53s
450:	test: 0.9566415	best: 0.9568455 (407)	total: 2m 21s	remaining: 2m 52s
451:	test: 0.9565395	best: 0.9568455 (407)	total: 2m 22s	remaining: 2m 52s
452:	test: 0.9565395	best: 0.9568455 (407)	total: 2m 22s	remaining: 2m 52s
453:	test: 0.9566415	best: 0.9568455 (407)	total: 2m 22s	remaining: 2m 51s
454:	test: 0.9566415	best: 0.9568455 (407)	total: 2m 23s	remaining: 2m 51s
455:	test: 0.9567435	best: 0.9568455 (407)	total: 2m 23s	remaining: 2m 51s
456:	test: 0.9569476	best: 0.9569476 (456)	total: 2m 23s	remaining: 2m 50s
457:	test: 0.9569476	best: 0.9569476 (456)	total: 2m 24s	remaining: 2m 50s
458:	test: 0.9569476	best: 0.9569476 (456)	total: 2m 24s	remaining: 2m 50s
459:	test: 0.9569476	best: 0.9569476 (456)	total: 2m 24s	remaining: 2m 49s
460:	test: 0.9570496	best: 0.9570496 (460)	total: 2m 25s	remaining: 2m 49s
461:	test: 0.9570496	best: 0.9570496 (460)	total: 2m 25s	remaining: 2m 49s
462:	test: 0.9568455	best

559:	test: 0.9572536	best: 0.9573556 (551)	total: 2m 56s	remaining: 2m 18s
560:	test: 0.9572536	best: 0.9573556 (551)	total: 2m 56s	remaining: 2m 18s
561:	test: 0.9572536	best: 0.9573556 (551)	total: 2m 56s	remaining: 2m 17s
562:	test: 0.9572536	best: 0.9573556 (551)	total: 2m 57s	remaining: 2m 17s
563:	test: 0.9572536	best: 0.9573556 (551)	total: 2m 57s	remaining: 2m 17s
564:	test: 0.9571516	best: 0.9573556 (551)	total: 2m 57s	remaining: 2m 16s
565:	test: 0.9569476	best: 0.9573556 (551)	total: 2m 58s	remaining: 2m 16s
566:	test: 0.9570496	best: 0.9573556 (551)	total: 2m 58s	remaining: 2m 16s
567:	test: 0.9570496	best: 0.9573556 (551)	total: 2m 58s	remaining: 2m 15s
568:	test: 0.9571516	best: 0.9573556 (551)	total: 2m 59s	remaining: 2m 15s
569:	test: 0.9571516	best: 0.9573556 (551)	total: 2m 59s	remaining: 2m 15s
570:	test: 0.9571516	best: 0.9573556 (551)	total: 2m 59s	remaining: 2m 15s
571:	test: 0.9572536	best: 0.9573556 (551)	total: 3m	remaining: 2m 14s
572:	test: 0.9572536	best: 0.

In [198]:
predcat1 = ca1.predict(X_test6)
print(confusion_matrix(y_test6,predcat1))
print("Accuracy Score {}".format(accuracy_score(y_test6,predcat1)))
print("Classification report: {}".format(classification_report(y_test6,predcat1)))
print(f1_score(y_test6, predcat1, average="micro"))

[[ 42  16]
 [  4 165]]
Accuracy Score 0.9118942731277533
Classification report:               precision    recall  f1-score   support

           0       0.91      0.72      0.81        58
           1       0.91      0.98      0.94       169

    accuracy                           0.91       227
   macro avg       0.91      0.85      0.88       227
weighted avg       0.91      0.91      0.91       227

0.9118942731277533


In [52]:
X.dtypes[X.dtypes != 'int64'][X.dtypes != 'float64']

gender    object
dtype: object